_This notebook file is adapted from Melanie Walsh 2021 'Introduction to Cultural Analytics: Mapping' [https://melaniewalsh.github.io/Intro-Cultural-Analytics/Mapping/Mapping.html](https://melaniewalsh.github.io/Intro-Cultural-Analytics/Mapping/Mapping.html). You are encouraged to follow the remainder of her tutorial to learn how to add a custom map background, and how to publish your resulting map to the web._

# Mapping with Python

In this lesson, we're going to learn how to analyze and visualize geographic data.

# Geocoding with GeoPy

First, we're going to geocode data — aka get coordinates from addresses or place names — with the Python package [GeoPy](https://geopy.readthedocs.io/en/stable/#). GeoPy makes it easier to use a range of third-party [geocoding API services](https://geopy.readthedocs.io/en/stable/#), such as Google, Bing, ArcGIS, and OpenStreetMap.

Though most of these services require an API key, Nominatim, which uses OpenStreetMap data, does not, which is why we're going to use it here.

### Install GeoPy

In [1]:
!pip install geopy

     |████████████████████████████████| 112 kB 3.0 MB/s eta 0:00:01


### Import Nominatim

From GeoPy's list of possible geocoding services, we're going to import Nominatim:

In [2]:
from geopy.geocoders import Nominatim

### Nominatim & OpenStreetMap

<img src="https://upload.wikimedia.org/wikipedia/commons/thumb/b/b0/Openstreetmap_logo.svg/256px-Openstreetmap_logo.svg.png" border=2 >

Nominatim (which means "name" in Latin) uses [OpenStreetMap data](https://www.openstreetmap.org/relation/174979) to match addresses with geopgraphic coordinates. Though we don't need an API key to use Nominatim, we do need to create a unique [application name](https://operations.osmfoundation.org/policies/nominatim/). 

Here we're initializing Nominatim as a variable called `geolocator`. Change the application name below to your own application name:

In [3]:
geolocator = Nominatim(user_agent="GIVE-A-NAME-HERE-app", timeout=2)

To geocode an address or location, we simply use the `.geocode()` function:

In [6]:
location = geolocator.geocode("Wellington Street Ottawa")

In [7]:
location

Location(Wellington Street, Centretown, Somerset, (Old) Ottawa, Ottawa, Eastern Ontario, Ontario, K1P 5M4, Canada, (45.4227971, -75.6995593, 0.0))

---

### An Alternative: Google Geocoding API

The Google Geocoding API is superior to Nominatim, but it requires an API key and more set up. To enable the Google Geocoding API and get an API key, see [Get Started with Google Maps Platform](https://developers.google.com/maps/gmp-get-started) and [Get Started with Geocoding API](https://developers.google.com/maps/documentation/geocoding/start).

**If you want to just continue without mucking about with Google, skip down to the heading 'Continue'**

In [5]:
# once you get an API Key from Google, you would uncomment the three lines below,
# inserting the API key into the appropriate spot in the second line

#from geopy.geocoders import GoogleV3
#google_geolocator = GoogleV3(api_key="YOUR-API-KEY HERE")
#google_geolocator.geocode("Wellington Street")

### Get Address

In [8]:
print(location.address)

South Cayuga Street, South Hill, Ithaca, Ithaca Town, Tompkins County, New York, 14850, United States of America


### Get Latitude and Longitude

In [9]:
print(location.latitude, location.longitude)

42.4359281 -76.4988639


### Get "Importance" Score

In [10]:
print(f"Importance: {location.raw['importance']}")

Importance: 0.4


### Get Class and Type

In [11]:
print(f"Class: {location.raw['class']} \nType: {location.raw['type']}")

Class: highway 
Type: residential


---

## Continue...

### Get Multiple Possible Matches

In [8]:
possible_locations = geolocator.geocode("Wellington Street", exactly_one=False)

for location in possible_locations:
    print(location.address)
    print(location.latitude, location.longitude)
    print(f"Importance: {location.raw['importance']}")

Wellington Street, Centretown, Somerset, (Old) Ottawa, Ottawa, Eastern Ontario, Ontario, K1P 5C7, Canada
45.4227971 -75.6995593
Importance: 0.5492354726566488
Wellington Street, Centretown, Somerset, (Old) Ottawa, Ottawa, Eastern Ontario, Ontario, K1A 0A3, Canada
45.4234495 -75.6980579
Importance: 0.5492354726566488
Wellington Street, Centretown, Somerset, (Old) Ottawa, Ottawa, Eastern Ontario, Ontario, K1P 5M4, Canada
45.4227971 -75.6995593
Importance: 0.5492354726566488
Wellington Street, Newtown, Widnes, Halton, North West England, England, WA8 0BF, United Kingdom
53.3568398 -2.7350504
Importance: 0.3
Wellington Street, Newtown, Widnes, Halton, North West England, England, WA8 0QD, United Kingdom
53.3565607 -2.7353103
Importance: 0.3
Wellington Street, Modelpark, Emalahleni Ward 24, eMalahleni, Emalahleni Local Municipality, Nkangala, Mpumalanga, South Africa
-25.8653092 29.25061099581582
Importance: 0.3
Wellington Street, Mascot, Sydney, Bayside Council, New South Wales, 2020, Aust

In [10]:
location = geolocator.geocode("Wellington Street, Ottawa Ontario")

print(location.address)
print(location.latitude, location.longitude)
print(f"Importance: {location.raw['importance']}")

Wellington Street, Centretown, Somerset, (Old) Ottawa, Ottawa, Eastern Ontario, Ontario, K1P 5M4, Canada
45.4227971 -75.6995593
Importance: 0.7692354726566488


## Geocode with Pandas

To geocode every location in a CSV file, we can use Pandas, make a Python function, and `.apply()` it to every row in the CSV file.

In [18]:
# you might need to uncomment the next line and run it to install pandas
# pandas is a package that lets you work with tabular data etc

#!pip install pandas

import pandas as pd
pd.set_option("max_rows", 400)
pd.set_option("max_colwidth", 400)

Here we make a function with `geolocator.geocode()` and ask it to return the address, lat/lon, and importance score:

In [19]:
def find_location(row):
    
    place = row['place']
    
    location = geolocator.geocode(place)
    
    if location != None:
        return location.address, location.latitude, location.longitude, location.raw['importance']
    else:
        return "Not Found", "Not Found", "Not Found", "Not Found"

To start exploring, let's read in a CSV file with a list of places in and around Ithaca.

In [23]:
ottawa_df = pd.read_csv("ottawa-places.csv")

In [24]:
ottawa_df

place
0           Carleton University
1          University of Ottawa
2              Senate of Canada
3               Chateau Laurier
4             Algonquin College
5                 Bayshore Mall
6  Britannia Beach Ottawa River

Now let's `.apply()` our function to this Pandas dataframe and see what results Nominatim's geocoding service spits out.

In [25]:
ottawa_df[['address', 'lat', 'lon', 'importance']] = ottawa_df.apply(find_location, axis="columns", result_type="expand")
ottawa_df

place  \
0           Carleton University   
1          University of Ottawa   
2              Senate of Canada   
3               Chateau Laurier   
4             Algonquin College   
5                 Bayshore Mall   
6  Britannia Beach Ottawa River   

                                                                                                                                                address  \
0                                 Carleton University, 1125, Colonel By Drive, Capital, (Old) Ottawa, Ottawa, Eastern Ontario, Ontario, K1S 5B7, Canada   
1             University of Ottawa, 75, Laurier Avenue East, Sandy Hill, Rideau-Vanier, (Old) Ottawa, Ottawa, Eastern Ontario, Ontario, K1N 6N5, Canada   
2                                                                                                             Senate, Reno No. 51, Saskatchewan, Canada   
3  Fairmont Château Laurier, 1, Rideau Street, Byward Market, Lowertown, Rideau-Vanier, (Old) Ottawa, Ottawa, Eastern Ontario, Ontario, K1N 8W5, Canada   
4                           Algonquin College, 1385, Woodroffe Avenue, Centrepointe, College, Nepean, Ottawa, Eastern Ontario, Ontario, K2G 1V8, Canada   
5                                             Bayshore Mall, 3300, Broadway Street, Broadway, Eureka, Humboldt County, California, 95502, United States   
6                                                                  Britannia Beach, Bay, Ottawa, (Old) Ottawa, Ottawa, Eastern Ontario, Ontario, Canada   

         lat         lon  importance  
0  45.385858  -75.695004    0.698423  
1  45.422527  -75.683390    0.822764  
2  49.273746 -109.705258    0.345000  
3  45.425601  -75.695253    0.448807  
4  45.349520  -75.755720    0.577866  
5  40.779649 -124.190233    0.559973  
6  45.365779  -75.801067    0.510000

**What do you notice about these results?** ☝️☝️☝️

# Making Interactive Maps

To map our geocoded coordinates, we're going to use the Python library [Folium](https://python-visualization.github.io/folium/). Folium is built on top of the popular JavaScript library [Leaflet](https://leafletjs.com/).

To install and import Folium, run the cells below:

In [11]:
!pip install folium

     |████████████████████████████████| 94 kB 2.1 MB/s eta 0:00:01
  Using cached requests-2.25.1-py2.py3-none-any.whl (61 kB)
  Using cached chardet-4.0.0-py2.py3-none-any.whl (178 kB)
     |████████████████████████████████| 153 kB 3.6 MB/s eta 0:00:01
  Using cached idna-2.10-py2.py3-none-any.whl (58 kB)


In [12]:
import folium

### Base Map

First, we need to establish a base map. This is where we'll map our geocoded Ithaca locations. To do so, we're going to call `folium.Map()`and enter the general latitude/longitude coordinates of the Ithaca area at a particular zoom.

(To find latitude/longitude coordintes for a particular location, you can use Google Maps, [as described here](https://support.google.com/maps/answer/18539?co=GENIE.Platform%3DDesktop&hl=en).)

In [28]:
ottawa_map = folium.Map(location=[45.42, -75.69], zoom_start=12)
ottawa_map

### Add a Marker

Adding a marker to a map is easy with Folium! We'll simply call `folium.Marker()` at a particular lat/lon, enter some text to display when the marker is clicked on, and then add it to our base map.

In [29]:
folium.Marker(location=[45.385858, -75.695004], popup="Crafting Digital History!").add_to(ottawa_map)
ottawa_map

### Add Markers From Pandas Data

To add markers for every location in our Pandas dataframe, we can make a Python function and `.apply()` it to every row in the dataframe.

In [30]:
def create_map_markers(row, map_name):
    folium.Marker(location=[row['lat'], row['lon']], popup=row['place']).add_to(map_name)

Before we apply this function to our dataframe, we're going to drop any locations that were "Not Found" (which would cause `folium.Marker()` to return an error).

In [32]:
found_ottawa_locations = ottawa_df[ottawa_df['address'] != "Not Found"]

In [33]:
found_ottawa_locations.apply(create_map_markers, map_name=ottawa_map, axis='columns')
ottawa_map

### Save Map

In [26]:
ottawa_map.save("Ottawa-map.html")

## Torn Apart / Separados

The data in this section was drawn from [Torn Apart / Separados Project](https://github.com/xpmethod/torn-apart-open-data). It maps the locations of Immigration and Customs Enforcement (ICE) detention facilities, as featured in [Volume 1](http://xpmethod.plaintext.in/torn-apart/volume/1/).

Go to [https://github.com/melaniewalsh/Intro-Cultural-Analytics/tree/master/book/data](https://github.com/melaniewalsh/Intro-Cultural-Analytics/tree/master/book/data) to get the data files for this next section OR insert the following string pattern into the file names as appropriate to load directly from the web:

eg, where the code says `ICE_df = pd.read_csv("../data/ICE-facilities.csv")` 

you'd change that to

`ICE_df = pd.read_csv("https://raw.githubusercontent.com/melaniewalsh/Intro-Cultural-Analytics/master/book/data/ICE-facilities.csv`)`

### Add a Circle Marker

There are a few [different kinds of markers](https://python-visualization.github.io/folium/quickstart.html#Markers) that we can add to a Folium map, including circles. To make a circle, we can call `folium.CircleMarker()` with a particular radius and the option to fill in the circle. You can explore more customization options in the [Folium documentation](https://python-visualization.github.io/folium/modules.html#folium.vector_layers.CircleMarker). We're also going to add a hover `tooltip` in addition to a `popup`.

In [38]:
def create_ICE_map_markers(row, map_name):
    
    folium.CircleMarker(location=[row['lat'], row['lon']], raidus=100, fill=True,
                popup=folium.Popup(f"{row['Name'].title()} <br> {row['City'].title()}, {row['State']}", max_width=200),
                  tooltip=f"{row['Name'].title()} <br> {row['City'].title()}, {row['State']}"
                 ).add_to(map_name)

In [35]:
ICE_df = pd.read_csv("https://raw.githubusercontent.com/melaniewalsh/Intro-Cultural-Analytics/master/book/data/ICE-facilities.csv")
ICE_df

lat         lon  adpSum    onWeb Flags  \
0    28.895000  -99.121200    8391  28.8950   NaN   
1    32.036600  -84.771800    8004  32.0366   NaN   
2    34.559200 -117.441000    7265  34.5592   NaN   
3    32.817700 -111.520000    7096  32.8177   NaN   
4    47.249100 -122.421000    6757  47.2491   NaN   
..         ...         ...     ...      ...   ...   
481  39.671492  -75.714329       1   0.0000   NaN   
482  26.204563  -98.270145       1   0.0000   NaN   
483  41.528728  -73.363545       1   0.0000   NaN   
484        NaN         NaN       1   0.0000   NaN   
485        NaN         NaN       1   0.0000   NaN   

                                              fulladdr    DETLOC  \
0                 566 VETERANS DRIVE PEARSALL TX 78061   STCDFTX   
1                        146 CCA ROAD LUMPKIN GA 31815   STWRTGA   
2                  10250 RANCHO ROAD ADELANTO CA 92301   ADLNTCA   
3                    1705 EAST HANNA RD. ELOY AZ 85131       EAZ   
4                     1623 E. J STREET TACOMA WA 98421   CSCNWWA   
..                                                 ...       ...   
481                    970 BROAD STREET NEWARK NJ 7102   NEWHOLD   
482  BENTSEN TOWER, 1701 W BUS HWY 83 MCALLEN TX 78501   USMS3TX   
483     BRIDGEWATER STATE HOSPITAL BRIDGEWATER MA 2324   MABSHOS   
484                Redacted Redacted Redacted Redacted  Redacted   
485                Redacted Redacted Redacted Redacted  Redacted   

                                    Name                           Address  \
0          SOUTH TEXAS DETENTION COMPLEX                566 VETERANS DRIVE   
1               STEWART DETENTION CENTER                      146 CCA ROAD   
2         ADELANTO ICE PROCESSING CENTER                 10250 RANCHO ROAD   
3         ELOY FEDERAL CONTRACT FACILITY               1705 EAST HANNA RD.   
4             NORTHWEST DETENTION CENTER                  1623 E. J STREET   
..                                   ...                               ...   
481                 NEW/INS OS HOLD ROOM                  970 BROAD STREET   
482  US MARSHALS (SOUTH DISTRICT, TEXAS)  BENTSEN TOWER, 1701 W BUS HWY 83   
483           BRIDGEWATER STATE HOSPITAL        BRIDGEWATER STATE HOSPITAL   
484                             Redacted                          Redacted   
485                             Redacted                          Redacted   

            City  ... ICE.Threat.Level.2 ICE.Threat.Level.3  \
0       PEARSALL  ...                112                311   
1        LUMPKIN  ...                344                365   
2       ADELANTO  ...                206                164   
3           ELOY  ...                154                232   
4         TACOMA  ...                166                174   
..           ...  ...                ...                ...   
481       NEWARK  ...                  0                  0   
482      MCALLEN  ...                  0                  0   
483  BRIDGEWATER  ...                  0                  0   
484     Redacted  ...                  0                  0   
485     Redacted  ...                  0                  0   

    No.ICE.Threat.Level  Facility.Operator FY17.Calendar.Days.in.Use  \
0                  1187                GEO                       372   
1                   671                CCA                       372   
2                   726                GEO                       372   
3                   785                CCA                       372   
4                   693                GEO                       372   
..                  ...                ...                       ...   
481                   1            FEDERAL                        37   
482                   0            FEDERAL                         0   
483                   0           HOSPITAL                         0   
484                   0                ORR                        17   
485                   0                NaN                         0   

In [40]:
US_map = folium.Map(location=[42, -102], zoom_start=4)
US_map

In [41]:
ICE_df = ICE_df.dropna(subset=['lat', 'lon'])

In [42]:
ICE_df.apply(create_ICE_map_markers, map_name=US_map, axis="columns")
US_map

## Choropleth Maps

```margin Choropleth Map
Choropleth map = a map where areas are shaded according to a value
```

The data in this section was drawn from [Torn Apart / Separados Project](https://github.com/xpmethod/torn-apart-open-data). This data maps the "cumulative ICE awards since 2014 to contractors by congressional district," as featured in [Volume 2](http://xpmethod.plaintext.in/torn-apart/volume/2/).

To create a chropleth map with Folium, we need to pair a "geo.json" file (which indicates which parts of the map to shade) with a CSV file (which includes the variable that we want to shade by).

The following data was drawn from [the Torn Apart / Separados project](https://github.com/xpmethod/torn-apart/tree/master/data/districts)

In [43]:
US_districts_geo_json = "../data/ICE_money_districts.geo.json"

In [44]:
US_districts_csv = pd.read_csv("../data/ICE_money_districts.csv")

In [45]:
US_districts_csv = US_districts_csv .dropna(subset=['districtName', 'representative'])

In [46]:
US_districts_csv

id   id2        state  districtNumber          districtName  \
0    5001500US0101   101      Alabama               1       ta-ordinal-st-m   
1    5001500US0102   102      Alabama               2       ta-ordinal-nd-m   
2    5001500US0103   103      Alabama               3       ta-ordinal-rd-m   
3    5001500US0104   104      Alabama               4       ta-ordinal-th-m   
4    5001500US0105   105      Alabama               5       ta-ordinal-th-m   
..             ...   ...          ...             ...                   ...   
432  5001500US5506  5506    Wisconsin               6       ta-ordinal-th-m   
433  5001500US5507  5507    Wisconsin               7       ta-ordinal-th-m   
434  5001500US5508  5508    Wisconsin               8       ta-ordinal-th-m   
435  5001500US5600  5600      Wyoming               0  ta-at-large-district   
436  5001500US7298  7298  Puerto Rico              98       ta-ordinal-th-m   

          party  \
0    republican   
1    republican   
2    republican   
3    republican   
4    republican   
..          ...   
432  republican   
433  republican   
434  republican   
435  republican   
436      no-rep   

                                                                      district_url  \
0             https://en.wikipedia.org/wiki/Alabama%27s_1st_congressional_district   
1             https://en.wikipedia.org/wiki/Alabama%27s_2nd_congressional_district   
2             https://en.wikipedia.org/wiki/Alabama%27s_3rd_congressional_district   
3             https://en.wikipedia.org/wiki/Alabama%27s_4th_congressional_district   
4             https://en.wikipedia.org/wiki/Alabama%27s_5th_congressional_district   
..                                                                             ...   
432         https://en.wikipedia.org/wiki/Wisconsin%27s_6th_congressional_district   
433         https://en.wikipedia.org/wiki/Wisconsin%27s_7th_congressional_district   
434         https://en.wikipedia.org/wiki/Wisconsin%27s_8th_congressional_district   
435      https://en.wikipedia.org/wiki/Wyoming%27s_at-large_congressional_district   
436  https://en.wikipedia.org/wiki/Puerto_Rico%27s_at-large_congressional_district   

                               representative  \
0                               Bradley Byrne   
1                                 Martha Roby   
2                                 Mike Rogers   
3                             Robert Aderholt   
4                                   Mo Brooks   
..                                        ...   
432                            Glenn Grothman   
433                                Sean Duffy   
434                            Mike Gallagher   
435                                Liz Cheney   
436  Resident Commissioner Jenniffer González   

                                                                                                                                                                                representative_photo_url  \
0                                                                                                                https://upload.wikimedia.org/wikipedia/commons/7/71/Rep_Bradley_Byrne_%28cropped%29.jpg   
1                                                                                           https://upload.wikimedia.org/wikipedia/commons/5/55/Martha_roby_113_congressional_portrait_%28cropped%29.jpg   
2                                                                                                       https://upload.wikimedia.org/wikipedia/commons/e/ee/Mike_Rogers_official_photo_%28cropped%29.jpg   
3                                                                                                          https://upload.wikimedia.org/wikipedia/commons/9/9f/Rep._Robert_B._Aderholt_%28cropped%29.jpg   
4                                                                                                               https://upload.wikimedia.org/wikipedia/commons/b/b6/Mo_Brooks_Portrait_%28cropped%29

In [47]:
US_map = folium.Map(location=[42, -102], zoom_start=4)

folium.Choropleth(
    geo_data = US_districts_geo_json,
    name = 'choropleth',
    data = US_districts_csv,
    columns = ['districtName', 'total_awards'],
    key_on = 'feature.properties.districtName',
    fill_color = 'GnBu',
    line_opacity = 0.2,
    legend_name= 'Total ICE Money Received'
).add_to(US_map)

US_map

### Add a Tooltip to Choropleth

In [48]:
tooltip = folium.features.GeoJson(
    US_districts_geo_json,
    tooltip=folium.features.GeoJsonTooltip(fields=['representative', 'state', 'party', 'total_value'], localize=True)
                                )
US_map.add_child(tooltip)
US_map